In [1]:
import pandas as pd
import numpy as np
import os
from sklearn.model_selection import train_test_split, KFold
import warnings
from numpy import savetxt
from numpy import loadtxt
warnings.filterwarnings("ignore")

/home/arslan/anaconda3/envs/solar/lib/python3.8/site-packages/scipy/__init__.py:146: UserWarning: A NumPy version >=1.16.5 and <1.23.0 is required for this version of SciPy (detected version 1.23.3
  warnings.warn(f"A NumPy version >={np_minversion} and <{np_maxversion}"


In [2]:
from sklearn.metrics import r2_score
import optuna
from sklearn.ensemble import BaggingRegressor,AdaBoostRegressor,GradientBoostingRegressor
from sklearn.neighbors import KNeighborsRegressor
from sklearn.tree import DecisionTreeRegressor
import xgboost as xgb
from sklearn.svm import SVR
from catboost import CatBoostRegressor, Pool
from sklearn.ensemble import RandomForestRegressor

In [3]:
train = loadtxt('Data_Set/efficiencyTrain.csv', delimiter=',')
label = loadtxt('Data_Set/efficiencylabel.csv', delimiter=',')

In [4]:
os.environ["CUDA_DEVICE_ORDER"]="PCI_BUS_ID"   # see issue #152
os.environ["CUDA_VISIBLE_DEVICES"]="4"

In [5]:
X_train, X_test, y_train, y_test = train_test_split(train, label, test_size=0.15, random_state=42)

# Optuna

In [6]:
def bossting_objectiveDecisionTreeRegressor(trail):
    result=[]
    random_state=42
    losses=['squared_error', 'absolute_error', 'huber', 'quantile']
    min_samples_split=trail.suggest_float('min_samples_split',0.001,1.0)
    number_of_splits=trail.suggest_int('number_of_splits',4,7)
    random_state=trail.suggest_int('random_state',4,50)
    min_samples_leaf=trail.suggest_float('min_samples_leaf',0.001,0.5)
    min_weight_fraction_leaf=trail.suggest_float('min_weight_fraction_leaf',0.0,0.5)
    min_impurity_decrease=trail.suggest_float('min_impurity_decrease',0.0,0.5)
    ccp_alpha=trail.suggest_float('ccp_alpha',0.0,10.5)


    max_depth=trail.suggest_int('max_depth',2,50)
    k_fold=KFold(n_splits=number_of_splits)

    params={x:y for (x,y) in trail.params.items() if x!='number_of_splits'}
    result=[]
    for tr, tst in k_fold.split(train,label):
        xgb_reg = DecisionTreeRegressor(**params)
        X_train, X_test, y_train, y_test = train[tr],train[tst],label[tr],label[tst]
        xgb_reg.fit(X_train, y_train)
        # Handle pruning based on the intermediate value.
        if trail.should_prune():
            print("Handle pruning based on the intermediate value.")
            raise optuna.TrialPruned()

        result.append(round(r2_score(y_test,xgb_reg.predict(X_test)),4))
            
    return np.average(result)

In [7]:
def bossting_objectiveAdaBoostRegressor(trail):
    result=[]
    n_estimators = trail.suggest_int('n_estimators',1,50)
    learning_rate=trail.suggest_float("learning_rate", 1e-3, 1e-1,log=True)
    random_state= trail.suggest_int('random_state',1,100)

    number_of_splits=trail.suggest_int('number_of_splits',4,7)
    k_fold=KFold(n_splits=number_of_splits)
    params={x:y for (x,y) in trail.params.items() if x!='number_of_splits'}
    for tr, tst in k_fold.split(train,label):
        reg = AdaBoostRegressor(**params)
        X_train, X_test, y_train, y_test = train[tr],train[tst],label[tr],label[tst]
        reg.fit(X_train, y_train)
        result.append(round(r2_score(y_test,reg.predict(X_test)),4))
            
    return np.average(result)

In [8]:
def bossting_objectiveCatBoostRegressor(trail):
    result=[]
    
    iterations = trail.suggest_int('iterations',3000,40000)
    learning_rate=trail.suggest_float("learning_rate", 1e-3, 1e-1,log=True)
    depth=trail.suggest_int('depth',2,16)
    random_seed = trail.suggest_int('random_seed',50,500)
    metric_period = trail.suggest_int('metric_period',100,500)
    od_wait = trail.suggest_int('od_wait',10,150)
    

    params={x:y for (x,y) in trail.params.items() if x!='number_of_splits'}
    params['loss_function'] = 'RMSE'
    params['eval_metric'] = 'RMSE'
    params['od_type'] = 'Iter'
    params['use_best_model'] = True
    params['verbose'] = False
    result=[]
    number_of_splits=trail.suggest_int('number_of_splits',4,7)
    k_fold=KFold(n_splits=number_of_splits)
    for tr, tst in k_fold.split(train,label):


        model_regressor = CatBoostRegressor(**params)

        X_train, X_test, y_train, y_test = train[tr],train[tst],label[tr],label[tst]
        model_regressor.fit(X_train, y_train, 
          eval_set=(X_test, y_test),  
          use_best_model=True,  
          plot= False   
         );
        
        # Handle pruning based on the intermediate value.
        if trail.should_prune():
            print("Handle pruning based on the intermediate value.")
            raise optuna.TrialPruned()

        result.append(round(r2_score(y_test,model_regressor.predict(X_test)),4))
            
    return np.average(result)

In [9]:
def bossting_objectiveKNeighborsRegressor(trail):
    result=[]
    n_neighbors = trail.suggest_int('n_neighbors',1,50)
    leaf_size= trail.suggest_int('leaf_size',1,100)
    p= trail.suggest_int('p',1,2)
    n_jobs = trail.suggest_int('n_jobs',2,8)


    number_of_splits=trail.suggest_int('number_of_splits',4,7)
    k_fold=KFold(n_splits=number_of_splits)
    params={x:y for (x,y) in trail.params.items() if x!='number_of_splits'}
    for tr, tst in k_fold.split(train,label):
        reg = KNeighborsRegressor(n_neighbors=3,leaf_size=leaf_size,p=p,n_jobs=n_jobs)
        X_train, X_test, y_train, y_test = train[tr],train[tst],label[tr],label[tst]
        reg.fit(X_train, y_train)
        result.append(round(r2_score(y_test,reg.predict(X_test)),4))
            
    return np.average(result)

In [10]:
def bossting_objectiveRandomForestRegressor(trail):
    random_state=42
    losses=['squared_error', 'absolute_error', 'huber', 'quantile']
    criterions=['friedman_mse', 'squared_error']
    criterion=trail.suggest_categorical('criterion',criterions)
    n_estimators=trail.suggest_int('n_estimators',50,500)
    min_samples_leaf=trail.suggest_float('min_samples_leaf',0.001,0.5)
    min_samples_split=trail.suggest_float('min_samples_split',0.001,1.0)
    min_weight_fraction_leaf=trail.suggest_float('min_weight_fraction_leaf',0.001,0.5)
    max_depth=trail.suggest_int('max_depth',2,50)
    n_jobs = trail.suggest_int('n_jobs',2,4)
#     verbose= trail.suggest_int('verbose',1,100)
    ccp_alpha=trail.suggest_float('ccp_alpha',0.5,0.9)
#     min_impurity_decrease=trail.suggest_float('min_impurity_decrease',0.001,100.0)
    
    number_of_splits=trail.suggest_int('number_of_splits',4,7)
    k_fold=KFold(n_splits=number_of_splits)
    params={x:y for (x,y) in trail.params.items() if x!='number_of_splits'}
    result=[]
    for tr, tst in k_fold.split(train,label):
        reg=RandomForestRegressor(**params)
        X_train, X_test, y_train, y_test = train[tr],train[tst],label[tr],label[tst]
        reg.fit(X_train, y_train)
        result.append(round(r2_score(y_test,reg.predict(X_test)),4))
    return np.average(result)

In [11]:
def bossting_objectiveSVR(trail):
    result=[]
    coef0 = trail.suggest_float("coef0", 0.0, 10.0)
    tol = trail.suggest_float("tol", 0.001, 1.0)
    epsilon = trail.suggest_float("epsilon", 0.1, 10.0)
    C = trail.suggest_float("C", 1.0, 10.0)
    degree = trail.suggest_int('degree',3,10)
    max_iter = trail.suggest_int('max_iter',-1,100)
    cache_size = trail.suggest_int('cache_size',10,400)

    params={x:y for (x,y) in trail.params.items() if x!='number_of_splits'}
    result=[]
    number_of_splits=trail.suggest_int('number_of_splits',4,7)
    k_fold=KFold(n_splits=number_of_splits)
    for tr, tst in k_fold.split(train,label):
        xgb_reg=SVR(**params)
        X_train, X_test, y_train, y_test = train[tr],train[tst],label[tr],label[tst]
        xgb_reg.fit(X_train, y_train)
        # Handle pruning based on the intermediate value.
        if trail.should_prune():
            print("Handle pruning based on the intermediate value.")
            raise optuna.TrialPruned()

        result.append(round(r2_score(y_test,xgb_reg.predict(X_test)),4))
            
    return np.average(result)

In [12]:
def bossting_objectiveGradientBoostingRegressor(trail):
    result=[]
    learning_rate=trail.suggest_float("learning_rate", 1e-3, 1e-1,log=True)
    random_state=42
    losses=['squared_error', 'absolute_error', 'huber', 'quantile']
    # max_features=trail.suggest_float('max_features',0.001,1.0)
    alpha=trail.suggest_float('alpha',0.5,0.9)
    # ccp_alpha=trail.suggest_float('ccp_alpha',0.0,1)
    criterions=['friedman_mse', 'squared_error']
    loss=trail.suggest_categorical('loss',losses)
    criterion=trail.suggest_categorical('criterion',criterions)
    n_estimators=trail.suggest_int('n_estimators',50,500)
    number_of_splits=trail.suggest_int('number_of_splits',4,7)
    # subsample=trail.suggest_float('subsample',0.001,1.0)
    min_samples_leaf=trail.suggest_float('min_samples_leaf',0.001,0.5)
    min_samples_split=trail.suggest_float('min_samples_split',0.001,1.0)
    min_weight_fraction_leaf=trail.suggest_float('min_weight_fraction_leaf',0.001,0.5)
    max_depth=trail.suggest_int('max_depth',2,50)
    min_impurity_decrease=trail.suggest_float('min_impurity_decrease',0.001,100.0)
    k_fold=KFold(n_splits=number_of_splits)
    params={x:y for (x,y) in trail.params.items() if x!='number_of_splits'}
    result=[]
    for tr, tst in k_fold.split(train,label):
        reg=GradientBoostingRegressor(random_state=random_state,**params)
        X_train, X_test, y_train, y_test = train[tr],train[tst],label[tr],label[tst]
        reg.fit(X_train, y_train)
        result.append(round(r2_score(y_test,reg.predict(X_test)),4))
            
    return np.average(result)

In [13]:
optuna_Array = [bossting_objectiveDecisionTreeRegressor,bossting_objectiveAdaBoostRegressor,
               bossting_objectiveCatBoostRegressor,bossting_objectiveKNeighborsRegressor,
               bossting_objectiveRandomForestRegressor,bossting_objectiveSVR,bossting_objectiveGradientBoostingRegressor]

In [ ]:
study_array = []
for item in optuna_Array:
    study = optuna.create_study(direction="maximize")
    study.optimize(item, n_trials=5000)
    study_array.append(study)

[I 2023-05-22 09:41:17,666] A new study created in memory with name: no-name-fd5c7f3c-77aa-4eea-8928-7fcee59e1257
[I 2023-05-22 09:41:17,685] Trial 0 finished with value: -0.01037142857142857 and parameters: {'min_samples_split': 0.2669188765770386, 'number_of_splits': 7, 'random_state': 20, 'min_samples_leaf': 0.38547961387438545, 'min_weight_fraction_leaf': 0.4725976663733111, 'min_impurity_decrease': 0.042340356134896895, 'ccp_alpha': 1.8156425265066847, 'max_depth': 2}. Best is trial 0 with value: -0.01037142857142857.
[I 2023-05-22 09:41:17,698] Trial 1 finished with value: -0.020416666666666666 and parameters: {'min_samples_split': 0.37263006064172427, 'number_of_splits': 6, 'random_state': 33, 'min_samples_leaf': 0.3462375764948772, 'min_weight_fraction_leaf': 0.3558859657231609, 'min_impurity_decrease': 0.16653843792915213, 'ccp_alpha': 9.151834361907838, 'max_depth': 3}. Best is trial 0 with value: -0.01037142857142857.
[I 2023-05-22 09:41:17,708] Trial 2 finished with value: 

[I 2023-05-22 09:41:18,153] Trial 20 finished with value: -0.00375 and parameters: {'min_samples_split': 0.8086176354864076, 'number_of_splits': 4, 'random_state': 10, 'min_samples_leaf': 0.031446711359475216, 'min_weight_fraction_leaf': 0.42068246189734115, 'min_impurity_decrease': 0.06756522002722612, 'ccp_alpha': 1.8986189848969919, 'max_depth': 33}. Best is trial 4 with value: -0.00375.
[I 2023-05-22 09:41:18,186] Trial 21 finished with value: -0.00375 and parameters: {'min_samples_split': 0.6178144111156973, 'number_of_splits': 4, 'random_state': 24, 'min_samples_leaf': 0.4747157975833874, 'min_weight_fraction_leaf': 0.28185002742634857, 'min_impurity_decrease': 0.433846835431729, 'ccp_alpha': 0.7904778439569125, 'max_depth': 16}. Best is trial 4 with value: -0.00375.
[I 2023-05-22 09:41:18,220] Trial 22 finished with value: -0.00375 and parameters: {'min_samples_split': 0.03810704220747189, 'number_of_splits': 4, 'random_state': 4, 'min_samples_leaf': 0.4998684596625061, 'min_wei

[I 2023-05-22 09:41:18,898] Trial 41 finished with value: -0.00375 and parameters: {'min_samples_split': 0.8798815595985807, 'number_of_splits': 4, 'random_state': 14, 'min_samples_leaf': 0.038810681409557166, 'min_weight_fraction_leaf': 0.45586972056517827, 'min_impurity_decrease': 0.05098192678284244, 'ccp_alpha': 1.8955358166008434, 'max_depth': 37}. Best is trial 4 with value: -0.00375.
[I 2023-05-22 09:41:18,939] Trial 42 finished with value: -0.00375 and parameters: {'min_samples_split': 0.3203620972006088, 'number_of_splits': 4, 'random_state': 20, 'min_samples_leaf': 0.09782710344753842, 'min_weight_fraction_leaf': 0.3578192076097221, 'min_impurity_decrease': 0.04545786384976082, 'ccp_alpha': 9.258358826778458, 'max_depth': 33}. Best is trial 4 with value: -0.00375.
[I 2023-05-22 09:41:18,980] Trial 43 finished with value: -0.00375 and parameters: {'min_samples_split': 0.17351034745619714, 'number_of_splits': 4, 'random_state': 22, 'min_samples_leaf': 0.07001800823933035, 'min_

[I 2023-05-22 09:41:19,680] Trial 62 finished with value: -0.00375 and parameters: {'min_samples_split': 0.8498365436966542, 'number_of_splits': 4, 'random_state': 15, 'min_samples_leaf': 0.1268124616391326, 'min_weight_fraction_leaf': 0.0895665954723857, 'min_impurity_decrease': 0.11549619747499795, 'ccp_alpha': 8.525755036269237, 'max_depth': 46}. Best is trial 4 with value: -0.00375.
[I 2023-05-22 09:41:19,727] Trial 63 finished with value: -0.00375 and parameters: {'min_samples_split': 0.3836517319752504, 'number_of_splits': 4, 'random_state': 18, 'min_samples_leaf': 0.006039935407964321, 'min_weight_fraction_leaf': 0.3415401086219415, 'min_impurity_decrease': 0.14824282407063796, 'ccp_alpha': 4.525084043723204, 'max_depth': 39}. Best is trial 4 with value: -0.00375.
[I 2023-05-22 09:41:19,768] Trial 64 finished with value: -0.00375 and parameters: {'min_samples_split': 0.8382095053401928, 'number_of_splits': 4, 'random_state': 15, 'min_samples_leaf': 0.13730949027724004, 'min_weig

[I 2023-05-22 09:41:20,534] Trial 83 finished with value: -0.00375 and parameters: {'min_samples_split': 0.7119188520008054, 'number_of_splits': 4, 'random_state': 39, 'min_samples_leaf': 0.1942704588257758, 'min_weight_fraction_leaf': 0.133499870731346, 'min_impurity_decrease': 0.32772843699087595, 'ccp_alpha': 10.065717662223033, 'max_depth': 4}. Best is trial 4 with value: -0.00375.
[I 2023-05-22 09:41:20,569] Trial 84 finished with value: -0.00375 and parameters: {'min_samples_split': 0.4485164494871876, 'number_of_splits': 4, 'random_state': 13, 'min_samples_leaf': 0.21521561012394394, 'min_weight_fraction_leaf': 0.18701532987052574, 'min_impurity_decrease': 0.2790995444842341, 'ccp_alpha': 4.819203542499033, 'max_depth': 3}. Best is trial 4 with value: -0.00375.
[I 2023-05-22 09:41:20,606] Trial 85 finished with value: -0.00375 and parameters: {'min_samples_split': 0.6230994745522342, 'number_of_splits': 4, 'random_state': 12, 'min_samples_leaf': 0.14308702309113877, 'min_weight_

...

[I 2023-05-24 15:49:11,248] Trial 1654 finished with value: 0.363225 and parameters: {'iterations': 28624, 'learning_rate': 0.09983297872462392, 'depth': 12, 'random_seed': 451, 'metric_period': 253, 'od_wait': 38, 'number_of_splits': 4}. Best is trial 1335 with value: 0.3867.
[I 2023-05-24 15:51:31,310] Trial 1655 finished with value: 0.35080000000000006 and parameters: {'iterations': 29595, 'learning_rate': 0.07606713404404293, 'depth': 16, 'random_seed': 159, 'metric_period': 439, 'od_wait': 122, 'number_of_splits': 4}. Best is trial 1335 with value: 0.3867.
[I 2023-05-24 15:52:17,039] Trial 1656 finished with value: 0.3623 and parameters: {'iterations': 31977, 'learning_rate': 0.09021718241422513, 'depth': 15, 'random_seed': 212, 'metric_period': 260, 'od_wait': 111, 'number_of_splits': 4}. Best is trial 1335 with value: 0.3867.
[I 2023-05-24 15:55:28,669] Trial 1657 finished with value: 0.34975 and parameters: {'iterations': 31039, 'learning_rate': 0.02888375562780245, 'depth': 16

[I 2023-05-24 16:04:44,694] Trial 1666 finished with value: 0.34925 and parameters: {'iterations': 30581, 'learning_rate': 0.0830426461194473, 'depth': 14, 'random_seed': 175, 'metric_period': 236, 'od_wait': 117, 'number_of_splits': 4}. Best is trial 1335 with value: 0.3867.
[I 2023-05-24 16:05:23,352] Trial 1667 finished with value: 0.349725 and parameters: {'iterations': 32486, 'learning_rate': 0.09268720949978014, 'depth': 15, 'random_seed': 411, 'metric_period': 256, 'od_wait': 72, 'number_of_splits': 4}. Best is trial 1335 with value: 0.3867.
[I 2023-05-24 16:07:10,260] Trial 1668 finished with value: 0.3224 and parameters: {'iterations': 28379, 'learning_rate': 0.07508661359451257, 'depth': 16, 'random_seed': 160, 'metric_period': 244, 'od_wait': 37, 'number_of_splits': 5}. Best is trial 1335 with value: 0.3867.
[I 2023-05-24 16:07:39,779] Trial 1669 finished with value: 0.358525 and parameters: {'iterations': 24224, 'learning_rate': 0.08563473807420535, 'depth': 15, 'random_see

[I 2023-05-24 17:21:17,832] Trial 1675 finished with value: 0.34315 and parameters: {'iterations': 5593, 'learning_rate': 0.06435970013987038, 'depth': 15, 'random_seed': 181, 'metric_period': 423, 'od_wait': 123, 'number_of_splits': 4}. Best is trial 1335 with value: 0.3867.
[I 2023-05-24 17:21:43,745] Trial 1676 finished with value: 0.3517 and parameters: {'iterations': 31451, 'learning_rate': 0.09273320401661996, 'depth': 15, 'random_seed': 165, 'metric_period': 250, 'od_wait': 41, 'number_of_splits': 4}. Best is trial 1335 with value: 0.3867.
[I 2023-05-24 17:22:48,254] Trial 1677 finished with value: 0.362625 and parameters: {'iterations': 34925, 'learning_rate': 0.09999486206176807, 'depth': 16, 'random_seed': 170, 'metric_period': 274, 'od_wait': 38, 'number_of_splits': 4}. Best is trial 1335 with value: 0.3867.
[I 2023-05-24 17:23:02,327] Trial 1678 finished with value: 0.3459749999999999 and parameters: {'iterations': 5032, 'learning_rate': 0.07256557274994614, 'depth': 13, 'r

[I 2023-05-24 17:28:04,055] Trial 1684 finished with value: 0.34504999999999997 and parameters: {'iterations': 30916, 'learning_rate': 0.09174406758400024, 'depth': 16, 'random_seed': 174, 'metric_period': 412, 'od_wait': 31, 'number_of_splits': 4}. Best is trial 1335 with value: 0.3867.
[I 2023-05-24 17:29:46,680] Trial 1685 finished with value: 0.34685 and parameters: {'iterations': 16595, 'learning_rate': 0.09996935705201652, 'depth': 16, 'random_seed': 148, 'metric_period': 221, 'od_wait': 73, 'number_of_splits': 4}. Best is trial 1335 with value: 0.3867.
[I 2023-05-24 17:30:29,569] Trial 1686 finished with value: 0.3662 and parameters: {'iterations': 28081, 'learning_rate': 0.08464018260440481, 'depth': 15, 'random_seed': 157, 'metric_period': 335, 'od_wait': 84, 'number_of_splits': 4}. Best is trial 1335 with value: 0.3867.
[I 2023-05-24 17:31:07,372] Trial 1687 finished with value: 0.356 and parameters: {'iterations': 9816, 'learning_rate': 0.07880119540372091, 'depth': 15, 'ran

[I 2023-05-24 17:39:50,406] Trial 1694 finished with value: 0.3687 and parameters: {'iterations': 29073, 'learning_rate': 0.08656023900355539, 'depth': 15, 'random_seed': 161, 'metric_period': 365, 'od_wait': 78, 'number_of_splits': 4}. Best is trial 1335 with value: 0.3867.
[I 2023-05-24 17:41:55,926] Trial 1695 finished with value: 0.347525 and parameters: {'iterations': 24309, 'learning_rate': 0.07702478881988334, 'depth': 16, 'random_seed': 170, 'metric_period': 264, 'od_wait': 94, 'number_of_splits': 4}. Best is trial 1335 with value: 0.3867.
[I 2023-05-24 17:42:31,629] Trial 1696 finished with value: 0.341125 and parameters: {'iterations': 5343, 'learning_rate': 0.09238843848597687, 'depth': 15, 'random_seed': 224, 'metric_period': 256, 'od_wait': 47, 'number_of_splits': 4}. Best is trial 1335 with value: 0.3867.
[I 2023-05-24 17:43:48,473] Trial 1697 finished with value: 0.34425 and parameters: {'iterations': 6293, 'learning_rate': 0.06903667593162256, 'depth': 16, 'random_seed'

In [ ]:
for item in study_array:
    print('r2: ' + str(item.best_value))
    print('Best parameter: ' + str(item.best_params))

In [ ]:
optuna_Array[0]

In [ ]:
for item in study_array:
    fig = optuna.visualization.plot_param_importances(item)
    fig.show()

In [ ]:
def saveResults():
    a = open('Results/Efficiency.txt', 'w')
    a.write(study_array)
    a.close()

def getResults():
    f = open("Results/Efficiency.txt", "r")
    print(f)